In [ ]:
# Load in packages for pandas, astropy, etc. 

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from astropy.io import fits
from astropy.table import Table
from astropy.io import ascii
from astropy.table import Column, MaskedColumn
from astropy.io.ascii import masked
from astropy import units as u
from astropy.coordinates import SkyCoord
from astropy.cosmology import LambdaCDM 
from astroquery.simbad import Simbad
from astroquery.sdss import SDSS
from astropy.coordinates import match_coordinates_sky
import os 
import json 

cosmo = LambdaCDM(H0=70, Om0=0.3, Ode0=0.7) #Creating our choice of cosmology here...

pd.set_option('display.max_columns', 300) # Setting max number of rows per df to be the size of the df
pd.set_option('display.max_rows', None)



In [ ]:
# Formatting log
# 6 Dec. 2023
# Going to try to keep better track of changes as I'm doing them so I can add them as remarks to my commit notes
#
# Reformatting, reordering, and correcting system type labels. This involves removing duplicate entries, fixing \
# errors where a slash was missed during the matching process, system types missing altogether, and slimming down \
# the variations. For example, binary quasars --> dual AGNs or candidates, AGN recoil candidate --> \
# recoil candidate, etc., and we're removing things like 'fast jet realignment' and 'double-peak emitter'
# 
# These classes are going to be alphabetized from now on within the System Type cell. 
#
#
# I've noticed I accidently removed the separations for the Hennawi+2010 targets because they were referred to as \
# DelT (and vel diff was DelV). I've added the separations back in. Tytler+2009 is also missing info, but I think \
# I accidently removed it from their table when matching. I also corrected bibcodes --> BibCodes for Tytler+2009 \
# and Kirkman+2008. 
#
# Corrected the missing angular separations for Findlay+2018 (and converted from arcmin to arcsec). Also added \
# in coordinate waveband and source in for (SDSS or ATLAS), equinox, and changed Dual AGN--> Quasar Pair
# We'll remove pairs and keep genuine duals as we format here... Also ajusted the selection and confirmation \
# methods columns. 
#
# Added in the missing separations for Hennawi+2006 (removed them by accident). Correcting the selection and \
# confirmation methods of Hennawi+2006. This includes making adjustments to the t2 table. Separations have also \
# now been added back in for Hennawi+2010. These were being read in as delT_1
#
# In binary quasar notebook, also went back and fixed where I accidently was throwing out the BibCode(s) column
#
# Note for Hennawi's targets, we still have a problem. I was able to remove duplicates before, but I was not \
# careful about paying attention to whether the coordinates and redshifts referred to the same objects, or at least, \
# I have no record of being that careful. I will eventually need to go through by hand for all of the duplicates and \
# ensure the redshifts and coordinates do indeed refer to the same objects. For now, we will ignore this problem. 
#
# I believe I have now also fixed all of the equinox, coordinate waveband, and cordinate source info that was missing \
# from the binary quasar notebook (added back in where ever possible); made '1' and '2' columns for these entries
#
# Corrected the missing column in the Koss+2012 and Hainline+ listing
#
# Modified the selection method for targets from Yang+2019. These are no longer 'strong' and 'probable' X-shaped \
# radio sources; we list them simply as X-shaped radio sources. 
#
# Corrected the equinox, coordinate waveband, and coordinate course listings for X-shaped radio sources. Wrong \
# column names for some, others had wrong info (Yang+2019 for example had coordinates listed as optical and SDSS \
# rather than radio and VLA / FIRST)
#
# In individual table: (1) changed all 'Recoiling AGN Candidate' tags to 'Recoil Candidate'; (2) since X-shaped \
# radio sources have been claimed to be either recoiling AGNs/SMBHs AND binary AGNs, ALL X-shaped radio sources \
# have a 'recoil candidate' and a 'binary AGN candidate' tag. This is also the case in the actual X-shaped radio \
# source notebook; (3) removed use of 'double-peaked emitter candidate' from system types. no need to include.
#
# Appended '1' to all equinox, coordinate waveband, and coordinate source columns in varstrometry notebook. Also
# added in the z1 column (using the z column) in the Orosz table. No z column in the Hwang table, though. I have\
# now corrected issues with the Orosz+ table; RA1 and Dec1 have been added in, and RA2, Dec2, and Name2 have been \
# marked as -99 since no counterparts are currently known. Name2, RA2, Dec2, and the degree versions for the \
# Hwang+ table has also been flagged as -99. Note, the name flags are string(-99). RA1 and Dec1 added as well.
#
# Appended '1' to all equinox, coordinate waveband, and coordinate source columns in binary periodicity notebook.
# Also now added in a z1 column
#
# NEED TO ADD SELECTION METHOD INFO FOR THE MAJORITY OF LENS SELECTED SOURCES (ETC INADA 2008)
#
# In the offset eission line notebook, I've now added in the '1' entries for equinox, waveband, and source
#
# In the double-peaked notebook: (1) added 'candidate' to the object examined by Nandi+; (2) changed equinox, \
# coordinate waveband, and coordinate source columns to have '1' appended at the end; (3) added back in  the\
# redshift 1 column. All redshift 2s were verified to be identical to z1, and thenm overwritten to '-99' along \
# with the spec type and the dV entries. I also now fixed the issue of missing redshifts and coordinates for \
# a good chunk of the Yuan+2016 targets. The z column had been broken into z_x and z_y for some reason, so \
# =yuan2016['z'] obviously didnt work (I guess I coerced the errors away here by accident). Also added in the \
# sexagesimal format for coordinates under RA and Dec, which are then converted to RA1 and Dec1 at the end like \
# usual.
#
# In the offset broad line binary notebook: added in '1' and '2' entries for equinox, waveband, and source, and \
# verified that there are z1 columns. Redshift 2s were verified to be identical to z1s and overwritten by '-99'. \
# Spec types and dVs were also overwritte, except for the dVs from Kim+2016, which were based on Halpha.
#
# In the match all catalogs notebook, I think I fixed the issue where confirmation methods and names were being \
# overwritten by accident for one or two objects. I've also now fixed the issue where a system type flag from one \
# table was beeing added to the MAC without a delimiter.
#
# The dual quasars from lens searches seems okay for now, but I'll be checking for issues tomorrow (today) when \
# I output the latest version of the DR.
#
# Corrected the improper system type adding in the match all catalogs notebook. 
# In binary quasar notebook, changed 'quasar pairs' to quasar pair.
# In individual objects table, changed the Lusso+2019 target from dual quasar to dual agn. This will probably \
# get changed back to something else since this object is likely not a merger induced 'dual'
#
#
# In the lens matching notebook: I have now reformatted the redshift columns for Lemon2020 (z1-z2 because they \
# are NIQs). For cases of missing RA and Decs, I made sure to change it from str(-99) to -99. Reformatted Lemon \
# 2019 and 2018 as well, adjusting the redshifts for 1 and 2 (adding in z1, and making sure z1=z2 for NIQs), and \
# adjusted the string vs nonstring for coordinates of 2. Added in Name1 for Agnello and adjusted the 2 coords to \
# non strings. Agnello already has a redshift 1 column. Adjusted coord for 2 for Spiniello. I've made adjustments \
# to the eftek2017 table; I'd only previously adjusted z1 based on if z1<0, but now I adjust both z1 and 2 based \
# on the -1 flag, and I also modify the z type. I've formatted some of the equinox, waveband, and source entries \
# in more2016. See notes below about the Inada tables; I have done some major reformatting of the Inada csv input \
# files as well as adding for loopd top overwrite bad redshift, z type, and coordinate cells. I've finished adding \
# back in the (largely blank) notes column and finalizing changes to the lens notebook.
#
# It looks like some inconclusive pairs from some of Lemon's works are included (from 2019 I think) while others \
# (like in 2018) are excluded, even those not listed as being possible stars. We will need to come back to this \
# in a later release...
#
# Discovered a major issue wit the Inada2010t3 table. I had not properly accounted for redshifts that were 0 or \
# negative flags, and I cut on dV. As far as I am aware, this is the only time I did this in that notebook. This \
# threw out a bunch of objects, and several of these DO match with the BQ lists. I have now output that list of \
# 'lost' objects as a separate .csv and I will load it in and match it against the MAC in the matching catalog \
# notebook. Evidently I did the same thing to the 2012 notebook. I've output another .csv file for those 'lost' \
# sources as well. I've double-checked the formatting of the Inada+ cells (and the input files) to make sure the \
# redshift columns are fine and that coordinate columns to not contain strings. I've also added in aseveral for \
# loops to overwrite bad redshift values and bad redshift type entries. 
#
# In the catalog matching notebook, I now have addition cells at the end that match the missing objects from Inada \
# 2010 and 2012 back in, and concatenates the remaining objects with the MAC main tables.
#
#
# found and fixed a bug in the match catalogs. I had indiv instead of indiv_x in a few instances when matching \
# the individual tables against the main table.

# In the X-shaped radio source noteook: corrected the seleciton method for one of the cheung2007 tables. I've \
# also just updated the cell that adds Roberts+ info to the Cheung+ targets. It now grabs the redshifts from \
# Roberts+ if there is no redshift from Cheung+.

# In the individual table, I've now added a redshift for NGC 1068
# Adjusted the matching stuff for the Barrows+2011 target so that a secondary z and name are not adopted
# Added 'bulge' and 'red blob' in name1 and name2 for the Markakis+ target

# Just realized that I was starting to adjust the RA and Dec entries in my notebooks (like marking duplicate RA \
# and Dec 2 as -99), but I CANNOT do that without messing up the total matching notebook, because then these \
# objects will be placed in the MACnoRA2 table and will be matched differently. 

#
# Just discovered an issue with the varstrometry table from Hwang+; I didn't realize it at the time, but they have \
# duplicate entries, because where objects had two GAIA matches, they placed the second match on a second row \
# instead of using separate columns... 
#    At this point, it might be easier to just go in and manually correct the secondary coordinates and drop the \
# 'duplicate rows'... we'll have to see...
#
#
# Another issue noticed: Ra and Dec values for gattano are -99 for some reason, but I can see matches with \
#    Inada+2010.... need to look into this issue...
#
# Corrected the coordinates for the Wang+2010 IRAS target. Also correcting the Pindor coordinates in the \
# individual table (since in the matching script I have it overwrite from the individual table)

# WE NEED TO DOUBLE CHECK WHY DV AND SEP IS NOT TAKEN FROM FU2012T3 AND T4!S
#

# Down below, I've now finished overwriting all of the duplicate Name2 values in the binary/recoil table (there \
# are some dual candidates int hat table that weren't piocked up by the other table, but that's okay)

# As of 18 December, I am now adding in a confidence flag column. It will start as -99, and change to our -1-->1 \
# system as we modify the flags for samples and individual targets


# pindor+2006 individual target, not overlapping with hennawi, has secondary coordinates relative to first




In [311]:
MAC = pd.read_csv('MAC_DR0p5_14Dec2023.csv', sep=',')

MAC.fillna(-99, inplace=True)

MAC['Confidence Flag'] = -99


In [262]:
def find_matches(names):
    name_dict = {}
    matches = []

    for name in names:
        # Remove 'SDSS' or 'SDSS ' from the name
        modified_name = name.replace('SDSS ', '').replace('SDSS', '')

        first_6_chars = modified_name[:7]
        if first_6_chars in name_dict:
            matches.append((name_dict[first_6_chars], name))
        else:
            name_dict[first_6_chars] = name

    return matches

names = MAC['Name1'].to_list()
matched_pairs = find_matches(names)
print(len(matched_pairs))

for pair in matched_pairs:
    print(f"Match found: {pair[0]} and {pair[1]}")
    
    

350
Match found: J011832.49-001030.0 and J011832.93+010930.8
Match found: J094446.69+145321.8 and J094446.91+543845.8
Match found: J103853.29+392151.2 and J103853.77+224908.7
Match found: J104150.01+343755.7 and J104150.74+384300.5
Match found: J115701.26+030338.6 and J115701.83+150104.2
Match found: J115832.63+371013.5 and J115832.68+303921.8
Match found: J120238.12+544735.5 and J120238.20+173155.1
Match found: J120802.08+094557.1 and J120802.65+140645.2
Match found: J121103.55+292506.8 and J121103.61+304758.7
Match found: J124415.00+013730.2 and J124415.78-015055.6
Match found: J124633.09+103538.4 and J124633.76+115347.9
Match found: J131543.68+554704.4 and J131543.99+521055.7
Match found: J134512.10+231504.6 and J134512.26-000803.7
Match found: J134928.65+160933.1 and J134928.92+053222.7
Match found: J135429.06+132757.3 and J135429.82+340947.1
Match found: J151553.79+324612.3 and J151553.86+030301.1
Match found: J151713.75+071106.2 and J151713.79+343714.6
Match found: J152813.29+165

In [312]:
# here I'm going to make a legacy column called 'legacy system type'
# I'll use this later oon when I want to come back and add in the legacy system types that others have used, like \
# 'binary quasar'

MAC['Legacy System Type'] = MAC['System Type']

# and now here we're going to replace all 'binary quasar' system types with 'dual AGNs', and simialrly for the \
# candidates...

types = MAC['System Type'].dropna().str.split(' / ')

# Step 2 and 3: Remove duplicates, alphabetize, and replace 'binary quasar' with 'dual AGN' in any context for each cell
def process_cell(cell):
    # Replace 'binary quasar' with 'dual AGN' in any context
    cell = [x.replace('Binary Quasar', 'Dual AGN') for x in cell]
    cell = [x.replace('Quasar Pair', 'Dual AGN') for x in cell]
    # Remove duplicates using set and then convert back to list
    unique_labels = list(set(cell))
    # Alphabetize the contents
    unique_labels.sort()
    return unique_labels

processed_types = types.apply(process_cell)

# Step 4: Join the contents back into a single string
MAC['Processed System Type'] = processed_types.apply(' / '.join)


In [313]:
gandalf = MAC[MAC['Processed System Type'].str.contains('Dual AGN', na=False)]

unique_combinations = gandalf['Processed System Type'].dropna().unique()

print(unique_combinations)
print(len(unique_combinations))


gandalf_grey = gandalf[(gandalf['z1']>0) & (gandalf['z2']<0)]
gandalf_white = gandalf[(gandalf['z1']>0) & (gandalf['z2']>0)]
saruman = gandalf[(gandalf['z1']<0) & (gandalf['z2']<0)]


['Dual AGN Candidate / Likely Single AGN' 'Dual AGN Candidate'
 'Dual AGN / Dual AGN Candidate'
 'Dual AGN Candidate / Offset AGN Candidate'
 'Dual AGN Candidate / Recoil Candidate' 'Dual AGN'
 'Binary AGN Candidate / Dual AGN Candidate'
 'Binary AGN Candidate / Dual AGN Candidate / Recoil Candidate'
 'Binary AGN Candidate / Binary SMBH Candidate / Dual AGN Candidate'
 'Binary SMBH Candidate / Dual AGN Candidate'
 'Binary AGN Candidate / Dual AGN' 'Dual AGN / Likely Single AGN']
12


In [314]:
bqoverlap = ['J115822.77+123518.5','J120727.09+140817.1','J123555.27+683627.0','J132022.54+305622.8',\
             'J141855.41+244108.9','J142604.32+071930.0','J143002.88+071411.3','J145826.72+544813.1',\
             'J150747.23+290333.2','J160603.02+290050.8','J163510.30+291116.1','J155330.23+223010.22']

for index, row in gandalf.iterrows():
    if 'Hennawi' in row['Paper(s)']:
        gandalf.at[index, 'Processed System Type'] = 'Dual AGN'
    elif 'J005113.94+002047.2' in row['Name1']:
        gandalf.at[index, 'Processed System Type'] = 'Dual AGN'
    elif 'J100602.14+071131.0' in row['Name1']:
        gandalf.at[index, 'Processed System Type'] = 'Dual AGN'
    elif 'J220634.97+000327.6' in row['Name1']:
        gandalf.at[index, 'Processed System Type'] = 'Dual AGN'
    elif 'SDSS J1120+6711A' in row['Name1']:
        gandalf.at[index, 'Processed System Type'] = 'Dual AGN'
    elif row['Name1'] in bqoverlap:
        gandalf.at[index, 'Processed System Type'] = 'Dual AGN'
    elif 'SDSS J171544.05+600835.7' in row['Name1']:
        gandalf.at[index, 'Processed System Type'] = 'Dual AGN Candidate' # this needs a flag of either -0.5 or -1
        # we're reclassifying Julie's 2011 target from Dual AGN --> Dual AGN Candidate
    elif row['Processed System Type']=='Dual AGN Candidate / Offset AGN Candidate':
        gandalf.at[index, 'Processed System Type'] = 'Dual AGN Candidate'
        # here we're overwriting Julie's offset AGN classification, because in all cases they were also dual candidates
        # we may need to come back and think about this some more, because Julie's work was selecting dual SMBH candidates \
        # within a single host galaxy, but some of the overlap (ex. with Xin Liu's targets) have large separations \
        # (ex. 70 kpc), so these targets are technically a dual within a dual.... but I don't think I trust that offset \
        # AGNs truly are tracing dual SMBHs. We can always come back and change this later.
    elif row['Processed System Type']=='Dual AGN Candidate / Likely Single AGN':
        gandalf.at[index, 'Processed System Type'] = 'Dual AGN Candidate'
        #'Dual AGN Candidate / Likely Single AGN' is both a dual AGN candidate based on Liu+2011 (so resolved spec pair),\
        # but ALSO a dual AGN candidate based on double-peak selection (Wang, and the followed up by others). \
        # Muller-sanchez followed up with radio and showed that the origin of the double-peak was still ambiguous, but \
        # all of the papers seem to point to the double-peaked AGN being a single AGN. Muller-sanchez's imaging did not \
        # cover both nuclei that Liu+ consider to be a pair, so the folks doing the double-peaked work did not focus on ]
        # the companion at ~6'' away. So we'll class this as a dual AGN candidate
        #
        # Users will have to be wary of these kinds of cases, because the subjective flag will probably be +0.5 here,\
        # but that will reflect the dual candidacy from Liu's work and NOT the candidacy of the double-peaked work
        #
    #J155330.23+223010.22 diff redshifts
    #J163510.30+291116.1 diff redshifts?, we'll handle this later
    #J150747.23+290333.2 diff redshifts but doesnt meet dV cut; we'll remove this later, put it int he bad table, and relabel as clustered QSOs
    #J145826.72+544813.1 diff z
    # J143002.88+071411.3 diff z
    # J142604.32+071930.0 diff z
    # J141855.41+244108.9 diff z?, we'll handle this later
    # J123555.27+683627.0 diff z 
    
pippin = gandalf[gandalf['Processed System Type']=='Dual AGN / Dual AGN Candidate / Recoil Candidate']

# Binary AGN Candidate / Dual AGN --> This is J09527, McGurk+2011's target that was also selected by Liu+2014
# Dual AGN Candidate / Recoil Candidate --> overlap between x-shaped radio sources and double peak and a couple individual targets
# Binary AGN Candidate / Dual AGN Candidate this is fine
# Binary AGN Candidate / Dual AGN Candidate / Recoil Candidate this is fine and is due to X-shaped radio source overlap
# Binary SMBH Candidate / Dual AGN Candidate --> just one target, and is fine


### Fixed:
# 'Dual AGN / Offset AGN Candidate' --> Originally from Liu, followed-up by husemann. Also selected by Barrows as \
# offset AGN, but I think after some reading, it will prob be marked as a dual AGN only.
# 'Dual AGN / Dual AGN Candidate' --> a lot of overlap between Hennawi and others, and then some with Liu2011 \
# and others
#'Dual AGN / Likely Single AGN' --> This is Julie Comerford's 2011 target, followed up by Liu, Smith, Smith, and others
# 'Dual AGN Candidate / Offset AGN Candidate' --> overlap between comerford+ and liu+2011, inada+2010, smith2010, \
# and liu2010
# 'Dual AGN Candidate / Likely Single AGN' see notes above
# 'Binary AGN Candidate / Binary SMBH Candidate / Dual AGN Candidate' --> This is J1536+0441
# Looking at how amyn people grabbed this target and for different reasons, I'm okay keeping this cross class

# note: when we add the Fu+ selection method, we overwrite the liu2011 selection method. make sure to fix this in the notebook.
# J005113.94+002047.2 --> confirmed binary in radio.
# J220634.97+000327.6 --> confirmed binary in radio.
# J100602.14+071131.0 --> I believe this is confirmed as a dual in the radio by rubinur but confirm
# SDSS J1120+6711A --> likely dual based on Pindor's work
# anything with hennawi+ gets pushed to dual agn status. 

# 2345+007 --> confirmed dual AGN ...
# myers+ targets, unless we have redshifts for both, are staying as dual candidates. If we have redshifts for \
# both and there is some dV, we'll consider them as duals with high confidence


pippin

Empty DataFrame
Columns: [Unnamed: 0, System Type, Literature Name, Selection Method, Confirmation Method, Name1, z1, z1_type, RA1, Dec1, Coordinate_waveband1, Coordinate_Source1, Equinox1, Brightness1, Brightness_band1, Brightness_type1, Name2, z2, z2_type, RA2, Dec2, Equinox2, Coordinate_waveband2, Coordinate_Source2, Brightness2, Brightness_band2, Brightness_type2, dV, Sep, Sep(kpc), dV_rwp, Paper(s), BibCode(s), DOI(s), Notes, Legacy System Type, Processed System Type]
Index: []

In [315]:
unique_combinations = gandalf['Processed System Type'].dropna().unique()

print(unique_combinations)
print(len(unique_combinations))



['Dual AGN Candidate' 'Dual AGN' 'Dual AGN Candidate / Recoil Candidate'
 'Binary AGN Candidate / Dual AGN Candidate'
 'Binary AGN Candidate / Dual AGN Candidate / Recoil Candidate'
 'Binary AGN Candidate / Binary SMBH Candidate / Dual AGN Candidate'
 'Binary SMBH Candidate / Dual AGN Candidate'
 'Binary AGN Candidate / Dual AGN']
8


In [316]:
aragorn = gandalf[(gandalf['RA1']==gandalf['RA2']) & gandalf['Dec1']==gandalf['Dec2']]

boromir = gandalf[(gandalf['RA1']==gandalf['RA2'])]

legolas = gandalf[gandalf['RA1']!=gandalf['RA2']]

print(len(aragorn),len(legolas),len(boromir))



0 4292 101


In [309]:
boromir


Unnamed: 0              System Type     Literature Name  \
2              2       Dual AGN Candidate                 NaN   
290          290       Dual AGN Candidate                 NaN   
1295        1295       Dual AGN Candidate                 NaN   
1335        1335            Binary Quasar                 NaN   
1558        1558  Binary Quasar Candidate                 NaN   
3135        3135       Dual AGN Candidate  IRAS 14348-1447 NE   

                                       Selection Method  \
2     Fiber Spectra / Optical Spectroscopic Emission...   
290   Fiber Spectra / Optical Spectroscopic Emission...   
1295                               Double Radio Sources   
1335                                    Optical Imaging   
1558                                 Optical Photometry   
3135                          IR Colors / X-ray Imaging   

            Confirmation Method                Name1       z1 z1_type  \
2                           -99  J000323.74+010547.3   0.0993    spec   
290        Optical Spectroscopy  J094741.58+633941.4   0.1397    spec   
1295                        -99   231953.40+003816.2 -99.0000     -99   
1335  Slit Optical Spectroscopy      SDSSJ1600+0000A   1.0110    spec   
1558                       -100  J115217.31-004746.2   1.5250    phot   
3135                        NaN   IRAS 14348-1447 NE   0.0830    spec   

                      RA1                 Dec1 Coordinate_waveband1  \
2             00:03:23.74          +01:05:47.3              Optical   
290           09:47:41.58          +63:39:41.4              Optical   
1295          23:19:53.40          +00:38:16.2              Optical   
1335            16:0:15.5            +0:0:45.5              Optical   
1558          11:52:17.32           -0:47:46.2              Optical   
3135  14:37:38.2867288488  -15:00:24.087592692              Optical   

     Coordinate_Source1 Equinox1 Brightness1     Brightness_band1  \
2                  SDSS    J2000       -99.0                  -99   
290                SDSS    J2000       -99.0                  -99   
1295               SDSS    J2000      -100.0               -100.0   
1335               SDSS    J2000       19.11  SDSS g PSF ext-corr   
1558               SDSS    J2000        21.0               SDSS g   
3135               GAIA    J2000         NaN                  NaN   

     Brightness_type1                Name2         z2 z2_type  \
2                 -99  J000323.74+010559.5   0.099400    spec   
290               -99  J094741.58+633939.2   0.139000    spec   
1295           -100.0   231953.40+003813.4 -99.000000     -99   
1335            asinh      SDSSJ1600+0000B   1.011000    spec   
1558        asinh mag  J115217.32-004750.1   2.075000    phot   
3135              NaN   IRAS 14348-1447 SW   0.082551    spec   

                      RA2                 Dec2 Equinox2 Coordinate_waveband2  \
2             00:03:23.74          +01:05:59.5    J2000              Optical   
290           09:47:41.58          +63:39:39.2    J2000              Optical   
1295          23:19:53.40          +00:38:13.4    J2000              Optical   
1335            16:0:15.5            +0:0:45.5    J2000              Optical   
1558          11:52:17.32           -0:47:50.2    J2000              Optical   
3135  14:37:38.2867288488  -15:00:24.087592692    J2000              Optical   

     Coordinate_Source2 Brightness2     Brightness_band2 Brightness_type2  \
2                  SDSS       -99.0                  -99              -99   
290                SDSS       -99.0                  -99              -99   
1295               SDSS      -100.0               -100.0           -100.0   
1335               SDSS         0.0  SDSS g PSF ext-corr            asinh   
1558               SDSS       20.79               SDSS g        asinh mag   
3135               GAIA         -99                  -99              -99   

         dV    Sep   Sep(kpc)      dV_rwp                    Paper(s)  \
2      22.0 

In [317]:
# and here we're going to fix up the duplicate Name1 and Name2s, duplicate coordinates between RA1 and RA2, etc...

for index, row in gandalf.iterrows():
    if row['Paper(s)'] == 'Hwang+2020':
        #gimli.at[index, 'Confidence Flag'] = -1
        gandalf.at[index, 'RA2'] = -99
        gandalf.at[index, 'Dec2'] = -99
        gandalf.at[index, 'Equinox2'] = -99
        gandalf.at[index, 'Coordinate_waveband2'] = -99
        gandalf.at[index, 'Coordinate_Source2'] = -99
    elif row['Paper(s)'] == 'Orosz+2013':
        gandalf.at[index, 'RA2'] = -99
        gandalf.at[index, 'Dec2'] = -99
        gandalf.at[index, 'Equinox2'] = -99
        gandalf.at[index, 'Coordinate_waveband2'] = -99
        gandalf.at[index, 'Coordinate_Source2'] = -99
    elif row['Paper(s)'] == 'Comerford+2013':
        gandalf.at[index, 'RA2'] = -99
        gandalf.at[index, 'Dec2'] = -99
        gandalf.at[index, 'Equinox2'] = -99
        gandalf.at[index, 'Coordinate_waveband2'] = -99
        gandalf.at[index, 'Coordinate_Source2'] = -99
    #elif row['Paper(s)'] == 'Gattano+2014':
    #    gandalf.at[index, 'RA2'] = -99
    #    gandalf.at[index, 'Dec2'] = -99
    #    gandalf.at[index, 'Equinox2'] = -99
    #    gandalf.at[index, 'Coordinate_waveband2'] = -99
    #    gandalf.at[index, 'Coordinate_Source2'] = -99

# nmeed to check pindor+hiennawi


# and below here, we'll start cleaning up the selection, analysis, and confirmation methdologies



In [ ]:
# and now adjusting the selection, analysis, and confirmation methodologies....








In [268]:
#list(pippin['Name1'])

In [172]:
# Function to check the condition
def check_value(value):
    if pd.isna(value) or (value != -99 and not value > 0):
        return True
    return False

# Applying the check and creating a new DataFrame
#filtered_df = gandalf[gandalf['z1'].apply(check_value)]

#print("Original DataFrame:")
#print(df)
#print("\nFiltered DataFrame:")
#filtered_df

# As of December 14/15th 2023, we have fixed all issues of NaN values in the redshift z1 and z2 column for duals


In [173]:
# running calculations for gandalf_white, where we have redshifts for both
gandalf_white['dV_new'] = -99

for index, row in gandalf_white.iterrows():
    gandalf_white.at[index, 'dV_new'] = (2.99e+5) * ((1 + row['z1'])**2 - (1 + row['z2'])**2) / ((1 + row['z1'])**2 + (1 + row['z2'])**2)
    gandalf_white.at[index, 'Sep(kpc)_z1'] = row['Sep']*cosmo.kpc_proper_per_arcmin(row['z1'])*(u.arcmin/u.kpc)*(1/60)
    gandalf_white.at[index, 'Sep(kpc)_z2'] = row['Sep']*cosmo.kpc_proper_per_arcmin(row['z2'])*(u.arcmin/u.kpc)*(1/60)

#gandalf_white['Sep(kpc)'] = gandalf_white['Sep']*cosmo.kpc_proper_per_arcmin(gandalf_white['z1'])*(u.arcmin/u.kpc)*(1/60)

# now to cull the stuff we're not interested in...

bad = gandalf_white[(np.abs(gandalf_white['dV_new'])>2000)] 
bad2 = gandalf_white[((gandalf_white['Sep(kpc)_z1']>110) & (gandalf_white['Sep(kpc)_z2']>110))]
print(len(bad),len(bad2))


/var/folders/_n/4v22wftn7354wlkmn_g7rtdr0000gn/T/ipykernel_30324/3510151646.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  gandalf_white['dV_new'] = -99
/var/folders/_n/4v22wftn7354wlkmn_g7rtdr0000gn/T/ipykernel_30324/3510151646.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  gandalf_white.at[index, 'dV_new'] = (2.99e+5) * ((1 + row['z1'])**2 - (1 + row['z2'])**2) / ((1 + row['z1'])**2 + (1 + row['z2'])**2)
/var/folders/_n/4v22wftn7354wlkmn_g7rtdr0000gn/T/ipykernel_30324/3510151646.py:6: SettingWit

152 326


In [174]:
bad

Unnamed: 0                                   System Type  \
1292        1292                            Dual AGN Candidate   
1294        1294                            Dual AGN Candidate   
1526        1526            Binary Quasar / Dual AGN Candidate   
1529        1529                       Binary Quasar Candidate   
1530        1530                       Binary Quasar Candidate   
1531        1531  Binary Quasar Candidate / Dual AGN Candidate   
1532        1532                       Binary Quasar Candidate   
1533        1533                       Binary Quasar Candidate   
1535        1535                       Binary Quasar Candidate   
1537        1537                       Binary Quasar Candidate   
1538        1538                       Binary Quasar Candidate   
1539        1539  Binary Quasar Candidate / Dual AGN Candidate   
1540        1540                       Binary Quasar Candidate   
1542        1542                       Binary Quasar Candidate   
1543        1543                       Binary Quasar Candidate   
1544        1544                       Binary Quasar Candidate   
1545        1545                       Binary Quasar Candidate   
1546        1546                       Binary Quasar Candidate   
1547        1547                       Binary Quasar Candidate   
1548        1548                       Binary Quasar Candidate   
1550        1550                       Binary Quasar Candidate   
1551        1551  Binary Quasar Candidate / Dual AGN Candidate   
1552        1552                       Binary Quasar Candidate   
1553        1553  Binary Quasar Candidate / Dual AGN Candidate   
1554        1554                       Binary Quasar Candidate   
1555        1555                       Binary Quasar Candidate   
1556        1556                       Binary Quasar Candidate   
1557        1557  Binary Quasar Candidate / Dual AGN Candidate   
1558        1558                       Binary Quasar Candidate   
1559        1559                       Binary Quasar Candidate   
1560        1560                       Binary Quasar Candidate   
1561        1561                       Binary Quasar Candidate   
1562        1562  Binary Quasar Candidate / Dual AGN Candidate   
1563        1563  Binary Quasar Candidate / Dual AGN Candidate   
1564        1564                       Binary Quasar Candidate   
1565        1565                       Binary Quasar Candidate   
1566        1566                       Binary Quasar Candidate   
1567        1567  Binary Quasar Candidate / Dual AGN Candidate   
1568        1568  Binary Quasar Candidate / Dual AGN Candidate   
1570        1570  Binary Quasar Candidate / Dual AGN Candidate   
1571        1571  Binary Quasar Candidate / Dual AGN Candidate   
1573        1573                       Binary Quasar Candidate   
1574        1574  Binary Quasar Candidate / Dual AGN Candidate   
1575        1575                       Binary Quasar Candidate   
1576        1576  Binary Quasar Candidate / Dual AGN Candidate   
1577        1577                       Binary Quasar Candidate   
1578        1578  Binary Quasar Candidate / Dual AGN Candidate   
1579        1579                       Binary Quasar Candidate   
1580        1580  Binary Quasar Candidate / Dual AGN Candidate   
1581        1581  Binary Quasar Candidate / Dual AGN Candidate   
1582        1582                       Binary Quasar Candidate   
1583        1583                       Binary Quasar Candidate   
1584        1584                       Binary Quasar Candidate   
1585        1585                       Binary Quasar Candidate   
1586        1586                       Binary Quasar Candidate   
1588        1588                       Binary Quasar Candidate   
1589        1589                       Binary Quasar Candidate   
1590        1590                       Binary Quasar Candidate   
1591        1591                       Binary Quasar Candidate   
1639        1639                              

In [175]:
bad2

Unnamed: 0                         System Type  \
1297        1297                       Binary Quasar   
1299        1299                       Binary Quasar   
1301        1301                       Binary Quasar   
1302        1302                       Binary Quasar   
1303        1303                       Binary Quasar   
1304        1304                       Binary Quasar   
1306        1306                       Binary Quasar   
1307        1307                       Binary Quasar   
1310        1310                       Binary Quasar   
1313        1313  Binary Quasar / Dual AGN Candidate   
1316        1316                       Binary Quasar   
1319        1319                       Binary Quasar   
1324        1324                       Binary Quasar   
1325        1325                       Binary Quasar   
1329        1329                       Binary Quasar   
1336        1336                       Binary Quasar   
1337        1337                       Binary Quasar   
1338        1338                       Binary Quasar   
1339        1339                       Binary Quasar   
1340        1340                       Binary Quasar   
1341        1341                       Binary Quasar   
1342        1342                       Binary Quasar   
1343        1343                       Binary Quasar   
1344        1344                       Binary Quasar   
1345        1345                       Binary Quasar   
1346        1346            Binary Quasar / Dual AGN   
1347        1347                       Binary Quasar   
1348        1348                       Binary Quasar   
1349        1349                       Binary Quasar   
1350        1350                       Binary Quasar   
1351        1351                       Binary Quasar   
1352        1352                       Binary Quasar   
1353        1353                       Binary Quasar   
1354        1354                       Binary Quasar   
1355        1355                       Binary Quasar   
1356        1356                       Binary Quasar   
1357        1357                       Binary Quasar   
1358        1358                       Binary Quasar   
1360        1360                       Binary Quasar   
1361        1361                       Binary Quasar   
1362        1362                       Binary Quasar   
1363        1363                       Binary Quasar   
1364        1364                       Binary Quasar   
1365        1365                       Binary Quasar   
1366        1366                       Binary Quasar   
1367        1367                       Binary Quasar   
1368        1368                       Binary Quasar   
1369        1369                       Binary Quasar   
1370        1370                       Binary Quasar   
1371        1371                       Binary Quasar   
1372        1372                       Binary Quasar   
1374        1374                       Binary Quasar   
1375        1375                       Binary Quasar   
1376        1376                       Binary Quasar   
1378        1378                       Binary Quasar   
1379        1379                       Binary Quasar   
1380        1380                       Binary Quasar   
1381        1381                       Binary Quasar   
1382        1382            Binary Quasar / Dual AGN   
1383        1383                       Binary Quasar   
1384        1384            Binary Quasar / Dual AGN   
1385        1385                       Binary Quasar   
1386        1386                       Binary Quasar   
1387        1387                       Binary Quasar   
1388        1388                       Binary Quasar   
1389        1389                       Binary Quasar   
1390        1390                       Binary Quasar   
1391        1391                       Binary Quasar   
1392        1392                       Binary Quasar   
1393        1393                       Binary Quasar   
1394        1394              

In [176]:
print(np.max(gandalf_white['Sep(kpc)_z1']))
print(np.max(gandalf_white['Sep(kpc)_z2']))
print(np.max(gandalf_white['dV_new']))

3921.763328210202
3921.325603326474
234353.72418518155


In [269]:
print(len(gandalf),len(gandalf_grey),len(gandalf_white),len(saruman))

# okay, so the problem children in terms a of redshift 
# and fu2015 


# Orosz has partial redshift coverage. Hwang has no redshifts.
# I've added in the available redshifts for Lemon 2018, 2019, and 2020.
# Spiniello+ is simply going to be a problem. No redshifts and no separations listed. We'll have to reach out.
# Fu 2015 is lacking redshifts for most
# Eftek has a subset that do not have redshifts
# Rusu2019 is lacking redshifts for pretty much everything



4393 2178 1907 295


In [270]:
# running calculations for gandalf_grey, where we have redshifts for both
gandalf_grey['dV_new'] = -99

for index, row in gandalf_grey.iterrows():
    #gandalf_grey.at[index, 'dV_new'] = (2.99e+5) * ((1 + row['z1'])**2 - (1 + row['z2'])**2) / ((1 + row['z1'])**2 + (1 + row['z2'])**2)
    gandalf_grey.at[index, 'Sep(kpc)_z1'] = row['Sep']*cosmo.kpc_proper_per_arcmin(row['z1'])*(u.arcmin/u.kpc)*(1/60)

#gandalf_grey['Sep(kpc)'] = gandalf_grey['Sep']*cosmo.kpc_proper_per_arcmin(gandalf_grey['z1'])*(u.arcmin/u.kpc)*(1/60)

# now to cull the stuff we're not interested in...

#bad3 = gandalf_grey[(np.abs(gandalf_grey['dV_new'])>2000)] 
bad3 = gandalf_grey[(gandalf_grey['Sep(kpc)_z1']>110)]
print(len(bad3))

#<0.4 is a double peaked object


/var/folders/_n/4v22wftn7354wlkmn_g7rtdr0000gn/T/ipykernel_30324/1225631020.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  gandalf_grey['dV_new'] = -99
/var/folders/_n/4v22wftn7354wlkmn_g7rtdr0000gn/T/ipykernel_30324/1225631020.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  gandalf_grey.at[index, 'Sep(kpc)_z1'] = row['Sep']*cosmo.kpc_proper_per_arcmin(row['z1'])*(u.arcmin/u.kpc)*(1/60)


50


In [ ]:
gandalf_white

In [114]:
gandalf_grey

Unnamed: 0                                System Type Literature Name  \
1244        1244                         Dual AGN Candidate             NaN   
1245        1245                         Dual AGN Candidate             NaN   
1247        1247                         Dual AGN Candidate             NaN   
1248        1248                         Dual AGN Candidate             NaN   
1250        1250                         Dual AGN Candidate             NaN   
1251        1251                         Dual AGN Candidate             NaN   
1253        1253                         Dual AGN Candidate             NaN   
1255        1255                         Dual AGN Candidate             NaN   
1256        1256                         Dual AGN Candidate             NaN   
1258        1258                         Dual AGN Candidate             NaN   
1259        1259                         Dual AGN Candidate             NaN   
1261        1261                         Dual AGN Candidate             NaN   
1262        1262                         Dual AGN Candidate             NaN   
1263        1263                         Dual AGN Candidate             NaN   
1264        1264                         Dual AGN Candidate             NaN   
1265        1265                         Dual AGN Candidate             NaN   
1266        1266                         Dual AGN Candidate             NaN   
1267        1267                         Dual AGN Candidate             NaN   
1268        1268                         Dual AGN Candidate             NaN   
1269        1269                         Dual AGN Candidate             NaN   
1270        1270                         Dual AGN Candidate             NaN   
1271        1271                         Dual AGN Candidate             NaN   
1272        1272                         Dual AGN Candidate             NaN   
1274        1274                         Dual AGN Candidate             NaN   
1275        1275                         Dual AGN Candidate             NaN   
1276        1276                         Dual AGN Candidate             NaN   
1277        1277                         Dual AGN Candidate             NaN   
1278        1278                         Dual AGN Candidate             NaN   
1279        1279                         Dual AGN Candidate             NaN   
1281        1281                         Dual AGN Candidate             NaN   
1282        1282                         Dual AGN Candidate             NaN   
1283        1283                         Dual AGN Candidate             NaN   
1284        1284                         Dual AGN Candidate             NaN   
1285        1285                         Dual AGN Candidate             NaN   
1288        1288                         Dual AGN Candidate             NaN   
1290        1290                         Dual AGN Candidate             NaN   
1291        1291                         Dual AGN Candidate             NaN   
1293        1293                         Dual AGN Candidate             NaN   
1295        1295                         Dual AGN Candidate             NaN   
1823        1823                         Dual AGN Candidate             NaN   
1824        1824                         Dual AGN Candidate             NaN   
1825        1825                         Dual AGN Candidate             NaN   
1826        1826                         Dual AGN Candidate             NaN   
1828        1828                         Dual AGN Candidate             NaN   
1829        1829                         Dual AGN Candidate             NaN   
1830        1830                         Dual AGN Candidate             NaN   
1831        1831                         Dual AGN Candidate             NaN   
1832        1832                         Dual AGN Candidate             NaN   
1833        1833                         Dual AGN Candidate             NaN   
1834        1834                         Dual AGN Candid

In [318]:
# carving up the table now to format individual pieces (hopefully this will make it easier to format... \
# it's been nothing but headaches so far...)


gimli = MAC[~MAC['Name1'].isin(gandalf['Name1'])]
print(len(MAC),len(gandalf),len(gimli))


# correcting system types and adding some confidence flags here....
for index, row in gimli.iterrows():
    if 'Single AGNs' in row['Processed System Type']:
        #gimli.at[index, 'Confidence Flag'] = -1
        gimli.at[index, 'Processed System Type'] = 'Dual AGN Candidate'
    elif 'Single AGN' in row['Processed System Type']:
        #gimli.at[index, 'Confidence Flag'] = -1
        gimli.at[index, 'Processed System Type'] = 'Dual AGN Candidate'
    elif 'Likely Single AGN' in row['Processed System Type']:
        #gimli.at[index, 'Confidence Flag'] = -1
        gimli.at[index, 'Processed System Type'] = 'Dual AGN Candidate'
    elif "J0045+41" in row['Name1']:
        #gimli.at[index, 'Confidence Flag'] = -1
        print('Adjusted')
    elif 'Offset AGN Candidate' in row['Processed System Type']:
        #gimli.at[index, 'Confidence Flag'] = 0
        gimli.at[index, 'Processed System Type'] = 'Dual SMBH Candidate'



unique_combinations = gimli['Processed System Type'].dropna().unique()

print(unique_combinations)
print(len(unique_combinations))


merry = gimli[gimli['Processed System Type']=='Binary SMBH Candidate']


### Fixed:
# AGN Recoil Candidate (Steinhardt+2012 target) --> changed to 'Recoil Candidate' in individual target list
# Binary AGN Candidate (Single AGN) --> changed to 'Binary AGn Candidate' in individual target list; this will get\
#     a flag of -1 in the catalog.
# Ejected Nucleus Candidate (this is the Keeney+2011 paper) --> changed this to recoil candidate. komossa+ \
#     refers to this work as a candidate, and Keeney+ also seem to suggest this could  be a recoil or ejected nucleus
# Binary SMBH Candidate / Dual SMBH Candidate / Recoil Candidate --> single menezes+2014 target
#    I'm okay with this classification until I check masses and compare against my binary definition.
# These are all converted back to dual AGN candidate, and a command has been added to insert a confidence flag:
#     Single AGNs --> these are the 2 single AGN objects from Fu+2015
#     Single AGN --> double-peaked selected, from varying samples
#     Likely Single AGN --> various double-peaked selection objects
## Offset AGN Candidate --> converting this to dual SMBH candidate in all cases

# Notes on flags to adjust:
#For literature name == LGGS J004527.30+413254.3, give flag of -1. Barth swiftly rejected this target.
# For the two 'Single AGNs'from Fu+2015a,b --> flag of -1 for these
# For the 'Single AGN' --> most likely flag -1 for these
# 'Likely Single AGN' --> most likely flag of -1 for these
# offset AGN candidate --> changing this to 'dual SMBH candidate' ? Since this is what Julie is trying to select \
# for. 

# Other things adjusted:
# Just finally added a redshift for NGC 1068
# Adjusted the matching stuff for the Barrows+2011 target so that a secondary z and name are not adopted
# Added 'bulge' and 'red blob' in name1 and name2 for the Markakis+ target

merry

6057 4393 1664
Adjusted
['Dual AGN Candidate' 'Binary AGN Candidate' 'Dual SMBH Candidate'
 'Recoil Candidate' 'Binary AGN Candidate / Recoil Candidate'
 'Binary AGN Candidate / Binary SMBH Candidate / Recoil Candidate'
 'Binary SMBH Candidate' 'Binary AGN'
 'Binary SMBH Candidate / Dual SMBH Candidate / Recoil Candidate']
9


Unnamed: 0            System Type Literature Name  \
3182           9  Binary SMBH Candidate        Arp 102B   
3183          10  Binary SMBH Candidate          3C 332   
3186          13  Binary SMBH Candidate          3C 120   
3189          16  Binary SMBH Candidate        3C 390.3   
3190          17  Binary SMBH Candidate        1928+738   
3195          22  Binary SMBH Candidate          3C 66B   
3198          25  Binary SMBH Candidate          3C 345   
3320         147  Binary SMBH Candidate           Mrk 6   

                                       Selection Method  \
3182  Double-Peaked Optical Spectroscopic Emission L...   
3183  Double-Peaked Optical Spectroscopic Emission L...   
3186   Optical Light Curve Variability / Jet Precession   
3189  Optical Spectroscopy / Double-Peaked Optical S...   
3190                                      Radio Imaging   
3195                                                -99   
3198                       Jet Precession / Variability   
3320                                      Radio Imaging   

                                 Confirmation Method     Name1       z1  \
3182                                             -99  Arp 102B  0.02417   
3183                                             -99    3C 332  0.15100   
3186                                             -99    3C 120  0.03300   
3189                                             -99  3C 390.3  0.06000   
3190                                             -99  1928+738  0.30000   
3195  VLBI Phase Reference Imaging / Periodicity****    3C 66B  0.02150   
3198                                     VLA Imaging    3C 345  0.59280   
3320                                   Radio Imaging     Mrk 6  0.01951   

     z1_type                  RA1                 Dec1 Coordinate_waveband1  \
3182     -99     17:19:14.4925747     +48:58:49.426017                Radio   
3183    spec  16:17:42.5380089648  +32:22:34.372277976              Optical   
3186    spec  04:33:11.0958197353  +05:21:15.617543663              Optical   
3189    spec  18:42:08.9910523393  +79:46:17.129210139              Optical   
3190    spec  19:27:48.4944745594  +73:58:01.571908984              Optical   
3195    spec       02:23:11.41124       +42:59:31.3840                Radio   
3198    spec  16:42:58.8100340220  +39:48:36.999540578              Optical   
3320    spec         06:52:12.251         +74:25:37.46                  -99   

     Coordinate_Source1 Equinox1 Brightness1 Brightness_band1  \
3182               VLBA    J2000       14.81                V   
3183               GAIA    J2000         -99              -99   
3186               Gaia    J2000       15.05                V   
3189               Gaia    J2000       15.38                V   
3190               Gaia    J2000        15.5                V   
3195               ICRF    J2000       14.81                V   
3198               Gaia    J2000       16.59                V   
3320                -99    J2000         -99              -99   

     Brightness_type1 Name2    z2 z2_type  RA2 Dec2 Equinox2  \
3182              mag   -99 -99.0     -99  -99  -99      -99   
3183              -99   -99 -99.0     -99  -99  -99      -99   
3186              mag   -99 -99.0     -99  -99  -99      -99   
3189              mag   -99 -99.0     -99  -99  -99      -99   
3190              mag   -99 -99.0     -99  -99  -99      -99   
3195              mag   -99 -99.0     -99  -99  -99      -99   
3198              mag   -99 -99.0     -99  -99  -99      -99   
3320              -99   -99 -99.0     -99  -99  -99      -99   

     Coordinate_waveband2 Coordinate_Source2 Brightness2 Brightness_band2  \
3182                  -99                -99         -99              -99   
3183                  -99                -99         -99              -99   
3186                  -99                -99         -99              -99   
3189                  -99                -99         -99              -99   
3190  

In [331]:
# and here we're going to fix up the duplicate Name1 and Name2s, duplicate coordinates between RA1 and RA2, etc...

name2fix = ['4C+22.25 / J1000+2233','084047.58+131223.5 / 3C 207','Abell 1145 / B1059+169 (Abell 1145)',\
            '3C 136.1 / 3C136.1','3C 315 / 3C315','3C 403 / 3C403','3C 52 / 3C52','4C 01.30 / 4C +01.30',\
            '4C 12.03 / 4C12.03','4C 48.29 / 4C48.29']

for index, row in gimli.iterrows():
    if row['RA1'] == row['RA2']:
        #gimli.at[index, 'Confidence Flag'] = -1
        gimli.at[index, 'RA2'] = -99
        gimli.at[index, 'Dec2'] = -99
        gimli.at[index, 'Equinox2'] = -99
        gimli.at[index, 'Coordinate_waveband2'] = -99
        gimli.at[index, 'Coordinate_Source2'] = -99
    elif row['Name1'] == row['Name2']:
        gimli.at[index, 'Name2'] = '-99'
    elif row['Name1'] == '3C 433 / 3C433':    
        gimli.at[index, 'Name2'] = '-99'
        gimli.at[index, 'RA2'] = -99
        gimli.at[index, 'Dec2'] = -99
    elif row['Literature Name'] == 'J093201.60+031858.7':    
        gimli.at[index, 'Name2'] = '-99'
    elif row['Name1'] in name2fix:    
        gimli.at[index, 'Name2'] = '-99'


# and below here, we'll start cleaning up the selection, analysis, and confirmation methdologies


In [320]:
gloin = gimli[(gimli['z1']>0) & (gimli['z2']<0)]
oin = gimli[(gimli['z1']>0) & (gimli['z2']>0)]
bombur = gimli[(gimli['z1']<0) & (gimli['z2']<0)]



In [332]:
kili = gimli[(gimli['RA1']!=gimli['RA2']) & (gimli['RA2']!=-99)]

print(len(kili))
kili

550


Unnamed: 0                                        System Type  \
1249        1249                                        Single AGNs   
1286        1286                                        Single AGNs   
3115        3115                                   Recoil Candidate   
3149        3149                                   Recoil Candidate   
3173           0                               Binary AGN Candidate   
3175           2  Recoil Candidate / Binary SMBH Candidate / Bin...   
3176           3                               Binary AGN Candidate   
3177           4  Binary AGN Candidate / Binary AGN Candidate / ...   
3178           5            Binary AGN Candidate / Recoil Candidate   
3179           6            Binary AGN Candidate / Recoil Candidate   
3181           8                               Binary AGN Candidate   
3182           9                              Binary SMBH Candidate   
3183          10                              Binary SMBH Candidate   
3184          11                               Binary AGN Candidate   
3186          13                              Binary SMBH Candidate   
3187          14                               Binary AGN Candidate   
3188          15                               Binary AGN Candidate   
3189          16                              Binary SMBH Candidate   
3190          17                              Binary SMBH Candidate   
3195          22                              Binary SMBH Candidate   
3197          24                                         Binary AGN   
3198          25                              Binary SMBH Candidate   
3202          29            Binary AGN Candidate / Recoil Candidate   
3203          30                               Binary AGN Candidate   
3204          31                               Binary AGN Candidate   
3205          32                                   Recoil Candidate   
3206          33                               Binary AGN Candidate   
3207          34                               Binary AGN Candidate   
3208          35                               Binary AGN Candidate   
3209          36                               Binary AGN Candidate   
3210          37                               Binary AGN Candidate   
3211          38                               Binary AGN Candidate   
3212          39                               Binary AGN Candidate   
3213          40                               Binary AGN Candidate   
3215          42                                   Recoil Candidate   
3216          43                               Binary AGN Candidate   
3220          47                                   Recoil Candidate   
3221          48                               Binary AGN Candidate   
3222          49                               Binary AGN Candidate   
3223          50                               Binary AGN Candidate   
3224          51                               Binary AGN Candidate   
3225          52                               Binary AGN Candidate   
3226          53                               Binary AGN Candidate   
3227          54                               Binary AGN Candidate   
3228          55                               Binary AGN Candidate   
3229          56                               Binary AGN Candidate   
3230          57                               Binary AGN Candidate   
3231          58                               Binary AGN Candidate   
3232          59                               Binary AGN Candidate   
3233          60                               Binary AGN Candidate   
3234          61                               Binary AGN Candidate   
3235          62                               Binary AGN Candidate   
3236          63                               Binary AGN Candidate   
3237          64                               Binary AGN Candidate   
3238          65                               Binary AGN Candidate   
3239          66              

In [333]:
fili = gimli[gimli['Name2']!='-99']

print(len(fili))
fili

9


Unnamed: 0           System Type      Literature Name  \
1249        1249           Single AGNs                  -99   
1286        1286           Single AGNs                  -99   
2206        2206  Offset AGN Candidate                  -99   
3115        3115      Recoil Candidate  CXOJ122518.6+144545   
3149        3149      Recoil Candidate             NGC 3718   
3184          11  Binary AGN Candidate               OJ 287   
3197          24            Binary AGN         CSO 0402+379   
3301         128      Recoil Candidate               3C 186   
3319         146      Recoil Candidate        ESO 1327-2041   

                                       Selection Method  \
1249                               Double Radio Sources   
1286                               Double Radio Sources   
2206  Velocity Offset Optical Spectroscopic Emission...   
3115  X-ray Imaging / Optical Imaging / Fiber Spectr...   
3149  Serendipitous / Near-IR Imaging / Radio Imagin...   
3184                        Serendipitous / Periodicity   
3197                      Serendipitous / Radio Imaging   
3301  Serendipitous / Near-IR Imaging / Optical Imaging   
3319                    Serendipitous / Optical Imaging   

                                    Confirmation Method  \
1249                                                      
1286                                                      
2206              -99 / Radio Imaging / Optical Imaging   
3115  Optical Imaging / X-ray Imaging / X-ray Spectr...   
3149  Near-IR Imaging / Radio Imaging / Optical Spec...   
3184                                                -99   
3197                                      Radio Imaging   
3301  Near-IR Imaging / UV Spectroscopy / Optical Sp...   
3319  Optical Imaging / Narrow-Band Optical Imaging ...   

                                     Name1         z1 z1_type  \
1249                    013412.78-010729.6   0.078900     -99   
1286                    222051.44+005815.0   0.318100     -99   
2206  J124135.09+285036.5 / KISSR 102 N1-A   0.066320    spec   
3115       CXOJ122518.6+144545 Off Nuclear -99.000000     -99   
3149                        NGC 3718 Bulge   0.003927    spec   
3184                                OJ 287   0.306000    spec   
3197                       CSO 0402+379 C1   0.055000    spec   
3301                           3C 186 HOST   1.068500    spec   
3319                  ESO 1327-2041 Galaxy   0.017810    spec   

                      RA1                 Dec1 Coordinate_waveband1  \
1249          01:34:12.78          -01:07:29.6              Optical   
1286          22:20:51.44          +00:58:15.0              Optical   
2206          12:41:35.09          +28:50:36.5              Optical   
3115         12:25:18.650          14:45:45.76                X-ray   
3149        11:32:34.8515        +53:04:04.475              Near-IR   
3184  08:54:48.8749311881  +20:06:30.642936668              Optical   
3197     04:05:49.2627587     +38:03:32.234373                Radio   
3301  07:44:17.4720658920  +37:53:17.250697320              Optical   
3319         13:30:05.302         -20:55:58.73                  -99   

     Coordinate_Source1 Equinox1 Brightness1 Brightness_band1  \
1249               SDSS    J2000      -100.0           -100.0   
1286               SDSS    J2000      -100.0           -100.0   
2206               SDSS    J2000      -100.0             -100   
3115            Chandra    J2000        26.4           g' mag   
3149             Subaru    J2000         -99              -99   
3184               Gaia    J2000       15.43                V   
3197               VLBA    J2000        18.5                V   
3301               GAIA    J2000         -99              -99   
3319                -99    J2000         -99              -99   

     Brightness_type1                                 Name2         z2  \
1249           -100.0                    013412.80-010724.8   0.078400   
1286           -100.0           

In [289]:
gloin

Unnamed: 0                                        System Type  \
1862        1862                               Binary AGN Candidate   
1863        1863                               Binary AGN Candidate   
1864        1864                               Binary AGN Candidate   
1865        1865                               Binary AGN Candidate   
1866        1866                               Binary AGN Candidate   
1867        1867                               Binary AGN Candidate   
1868        1868                               Binary AGN Candidate   
1869        1869                               Binary AGN Candidate   
1870        1870                               Binary AGN Candidate   
1871        1871                               Binary AGN Candidate   
1872        1872                               Binary AGN Candidate   
1873        1873                               Binary AGN Candidate   
1874        1874                               Binary AGN Candidate   
1875        1875                               Binary AGN Candidate   
1876        1876                               Binary AGN Candidate   
1877        1877                               Binary AGN Candidate   
1878        1878                               Binary AGN Candidate   
1879        1879                               Binary AGN Candidate   
1880        1880                               Binary AGN Candidate   
1881        1881                               Binary AGN Candidate   
1882        1882                               Binary AGN Candidate   
1883        1883                               Binary AGN Candidate   
1884        1884                               Binary AGN Candidate   
1885        1885                               Binary AGN Candidate   
1886        1886                               Binary AGN Candidate   
1887        1887                               Binary AGN Candidate   
1888        1888                               Binary AGN Candidate   
1889        1889                               Binary AGN Candidate   
1890        1890                               Binary AGN Candidate   
1891        1891                               Binary AGN Candidate   
1892        1892                               Binary AGN Candidate   
1893        1893                               Binary AGN Candidate   
1894        1894                               Binary AGN Candidate   
1895        1895                               Binary AGN Candidate   
1896        1896                               Binary AGN Candidate   
1897        1897                               Binary AGN Candidate   
1898        1898                               Binary AGN Candidate   
1899        1899                               Binary AGN Candidate   
1900        1900                               Binary AGN Candidate   
1901        1901                               Binary AGN Candidate   
1902        1902                               Binary AGN Candidate   
1903        1903                               Binary AGN Candidate   
1904        1904                               Binary AGN Candidate   
1905        1905                               Binary AGN Candidate   
1906        1906                               Binary AGN Candidate   
1907        1907                               Binary AGN Candidate   
1908        1908                               Binary AGN Candidate   
1909        1909                               Binary AGN Candidate   
1910        1910                               Binary AGN Candidate   
1911        1911                               Binary AGN Candidate   
1912        1912                               Binary AGN Candidate   
1913        1913                               Binary AGN Candidate   
1914        1914                               Binary AGN Candidate   
1915        1915                               Binary AGN Candidate   
1916        1916                               Binary AGN Candidate   
1917        1917              

In [285]:
oin

Unnamed: 0       System Type Literature Name  \
1249        1249       Single AGNs             NaN   
1286        1286       Single AGNs             NaN   
3149        3149  Recoil Candidate        NGC 3718   
3301         128  Recoil Candidate          3C 186   

                                       Selection Method  \
1249                               Double Radio Sources   
1286                               Double Radio Sources   
3149  Serendipitous / Near-IR Imaging / Radio Imagin...   
3301  Serendipitous / Near-IR Imaging / Optical Imaging   

                                    Confirmation Method               Name1  \
1249                                                     013412.78-010729.6   
1286                                                     222051.44+005815.0   
3149  Near-IR Imaging / Radio Imaging / Optical Spec...      NGC 3718 Bulge   
3301  Near-IR Imaging / UV Spectroscopy / Optical Sp...         3C 186 HOST   

            z1 z1_type                  RA1                 Dec1  \
1249  0.078900     -99          01:34:12.78          -01:07:29.6   
1286  0.318100     -99          22:20:51.44          +00:58:15.0   
3149  0.003927    spec        11:32:34.8515        +53:04:04.475   
3301  1.068500    spec  07:44:17.4720658920  +37:53:17.250697320   

     Coordinate_waveband1 Coordinate_Source1 Equinox1 Brightness1  \
1249              Optical               SDSS    J2000      -100.0   
1286              Optical               SDSS    J2000      -100.0   
3149              Near-IR             Subaru    J2000         NaN   
3301              Optical               GAIA    J2000         NaN   

     Brightness_band1 Brightness_type1               Name2        z2 z2_type  \
1249           -100.0           -100.0  013412.80-010724.8  0.078400     -99   
1286           -100.0           -100.0  222051.66+005815.8  0.317800     -99   
3149              NaN              NaN   NGC 3718 Red Blob  0.003927    spec   
3301              NaN              NaN       3C 186 Quasar  1.054000    spec   

                RA2           Dec2 Equinox2 Coordinate_waveband2  \
1249    01:34:12.80    -01:07:24.8    J2000              Optical   
1286    22:20:51.66    +00:58:15.8    J2000              Optical   
3149  11:32:34.8550  +53:04:04.512    J2000              Near-IR   
3301            -99            -99      -99                  -99   

     Coordinate_Source2 Brightness2 Brightness_band2 Brightness_type2     dV  \
1249               SDSS      -100.0           -100.0           -100.0  136.9   
1286               SDSS      -100.0           -100.0           -100.0   63.5   
3149             Subaru         NaN              NaN              NaN    NaN   
3301                -99         -99              -99              -99    NaN   

       Sep  Sep(kpc)  dV_rwp                         Paper(s)  \
1249  4.60     -99.0   -99.0               Fu+2015 ; Fu+2015b   
1286  2.60     -99.0   -99.0               Fu+2015 ; Fu+2015b   
3149  0.05       4.5     NaN                    Markakis+2015   
3301  1.32      11.0     NaN  Chiaberge+2017 ; Chiaberge+2018   

                                     BibCode(s)  \
1249  2015ApJ...799...72F ; 2015ApJ...815L...6F   
1286  2015ApJ...799...72F ; 2015ApJ...815L...6F   
3149                        2015A&A...580A..11M   
3301  2017A&A...600A..57C ; 2018ApJ...861...56C   

                                                 DOI(s)  \
1249  https://doi.org/10.1088/0004-637X/799/1/72 ; h...   
1286  https://doi.org/10.1088/0004-637X/799/1/72 ; h...   
3149        https://doi.org/10.1051/0004-6361/201425077   
3301  https://doi.org/10.1051/0004-6361/201629522 ; ...   

                                                  Notes Legacy System Type  \
1249  Faranoff-Riley II radio galaxies located withi...        Single AGNs   
1286  Faranoff-Riley II radio galaxies located withi...        Single AGNs   
3149  Markakis find an offset red blob in NIR imagin...   Recoil Candidate   
3301  Chiaberge+2017 me

In [290]:
bombur

Unnamed: 0                              System Type Literature Name  \
2489        2489  Binary AGN Candidate / Recoil Candidate             NaN   
2495        2495  Binary AGN Candidate / Recoil Candidate             NaN   
2496        2496  Binary AGN Candidate / Recoil Candidate             NaN   
2503        2503  Binary AGN Candidate / Recoil Candidate             NaN   
2507        2507  Binary AGN Candidate / Recoil Candidate             NaN   
2508        2508  Binary AGN Candidate / Recoil Candidate             NaN   
2511        2511  Binary AGN Candidate / Recoil Candidate             NaN   
2518        2518  Binary AGN Candidate / Recoil Candidate             NaN   
2521        2521  Binary AGN Candidate / Recoil Candidate             NaN   
2524        2524  Binary AGN Candidate / Recoil Candidate             NaN   
2525        2525  Binary AGN Candidate / Recoil Candidate             NaN   
2526        2526  Binary AGN Candidate / Recoil Candidate             NaN   
2528        2528  Binary AGN Candidate / Recoil Candidate             NaN   
2529        2529  Binary AGN Candidate / Recoil Candidate             NaN   
2530        2530  Binary AGN Candidate / Recoil Candidate             NaN   
2532        2532  Binary AGN Candidate / Recoil Candidate             NaN   
2533        2533  Binary AGN Candidate / Recoil Candidate             NaN   
2534        2534  Binary AGN Candidate / Recoil Candidate             NaN   
2535        2535  Recoil Candidate / Binary AGN Candidate             NaN   
2536        2536  Binary AGN Candidate / Recoil Candidate             NaN   
2538        2538  Binary AGN Candidate / Recoil Candidate             NaN   
2541        2541  Binary AGN Candidate / Recoil Candidate             NaN   
2542        2542  Binary AGN Candidate / Recoil Candidate             NaN   
2543        2543  Binary AGN Candidate / Recoil Candidate             NaN   
2545        2545  Binary AGN Candidate / Recoil Candidate             NaN   
2547        2547  Binary AGN Candidate / Recoil Candidate             NaN   
2551        2551  Binary AGN Candidate / Recoil Candidate             NaN   
2552        2552  Recoil Candidate / Binary AGN Candidate             NaN   
2553        2553  Binary AGN Candidate / Recoil Candidate             NaN   
2555        2555  Binary AGN Candidate / Recoil Candidate             NaN   
2557        2557  Binary AGN Candidate / Recoil Candidate             NaN   
2564        2564  Binary AGN Candidate / Recoil Candidate             NaN   
2566        2566  Binary AGN Candidate / Recoil Candidate             NaN   
2567        2567  Binary AGN Candidate / Recoil Candidate             NaN   
2569        2569  Binary AGN Candidate / Recoil Candidate             NaN   
2570        2570  Binary AGN Candidate / Recoil Candidate             NaN   
2571        2571  Binary AGN Candidate / Recoil Candidate             NaN   
2574        2574  Binary AGN Candidate / Recoil Candidate             NaN   
2576        2576  Binary AGN Candidate / Recoil Candidate             NaN   
2578        2578  Binary AGN Candidate / Recoil Candidate             NaN   
2583        2583  Binary AGN Candidate / Recoil Candidate             NaN   
2589        2589  Binary AGN Candidate / Recoil Candidate             NaN   
2590        2590  Binary AGN Candidate / Recoil Candidate             NaN   
2595        2595  Binary AGN Candidate / Recoil Candidate             NaN   
2597        2597  Binary AGN Candidate / Recoil Candidate             NaN   
2598        2598  Binary AGN Candidate / Recoil Candidate             NaN   
2599        2599  Binary AGN Candidate / Recoil Candidate             NaN   
2601        2601  Binary AGN Candidate / Recoil Candidate             NaN   
2604        2604  Binary AGN Candidate / Recoil Candidate             NaN   
2605        2605  Binary AGN Candidate / Recoil Candidate             NaN   
2606        2606  Binary AGN Candidate / Recoil Candidate             NaN   
26

In [ ]:
#for index, row in eftek2017.iterrows():
#    if (row['z1']!=-99) & (row['z2']!=-99):
#        eftek2017.at[index, 'dV'] = (2.99e+5)*((1+eftek2017.at[index,'z1'])**2 - (1+eftek2017.at[index,'z2'])**2)/((1+eftek2017.at[index,'z1'])**2+(1+eftek2017.at[index,'z2'])**2)
#    else:
#        eftek2017.at[index, 'dV'] = -99
        

In [230]:
4393+1664

6057

In [ ]:
gimli

In [ ]:
#unique_types = MAC['System Type'].dropna().unique()
#
#print("Unique System Types and combos:", unique_types)
#print(len(unique_types))


In [ ]:
binaries = MAC[(MAC['System Type']=='Binary AGN') | (MAC['System Type']=='Binary AGN Candidate') | \
               (MAC['System Type']=='Binary SMBH Candidate')]
print(len(binaries))

In [ ]:
binaries

In [ ]:
duals = MAC[MAC['System Type']=='Dual AGN']

print(len(duals))


In [ ]:
types = MAC['System Type'].dropna().str.split(' / ')

# Flatten the lists and find unique labels
unique_types = set(method for sublist in types for method in sublist)

print("Unique System Types and combos:", unique_types)
print(len(unique_types))



In [115]:
unique_combinations = MAC['Processed System Type'].dropna().unique()

print(unique_combinations)
print(len(unique_combinations))


['Dual AGN Candidate / Likely Single AGN' 'Dual AGN Candidate'
 'Dual AGN / Dual AGN Candidate'
 'Dual AGN Candidate / Offset AGN Candidate' 'Dual AGN'
 'Dual AGN Candidate / Recoil Candidate' 'Dual AGN / Offset AGN Candidate'
 'Binary AGN Candidate / Dual AGN Candidate' 'Single AGNs' 'Quasar Pair'
 'Binary AGN Candidate' 'Offset AGN Candidate' 'Likely Single AGN'
 'Binary AGN Candidate / Offset AGN Candidate / Recoil Candidate'
 'Recoil Candidate' 'Binary AGN Candidate / Recoil Candidate'
 'Binary AGN Candidate / Dual AGN Candidate / Recoil Candidate'
 'Binary AGN Candidate / Binary SMBH Candidate / Dual AGN Candidate'
 'Binary AGN Candidate / Binary SMBH Candidate / Recoil Candidate'
 'Binary SMBH Candidate' 'Binary SMBH Candidate / Dual AGN Candidate'
 'Binary AGN'
 'Binary SMBH Candidate / Dual SMBH Candidate / Recoil Candidate'
 'Ejected Nucleus Candidate' 'AGN Recoil Candidate'
 'Binary AGN Candidate (Single AGN)' 'Single AGN'
 'Dual AGN / Dual AGN Candidate / Recoil Candidate'
 

In [ ]:
for i,j in MAC.iterrows():
    if MAC.at[i, 'Processed System Type']=='Quasar Pairs':
        print(j)

In [ ]:
# here we're beginning to clean up the tables and remove projected pairs or pairs that are not close enough to \
# be 'merger-induced' (like clustered quasars)

# first we're checking to see if the coordinates and redshifts for AGN 1 and 2 are identical under some conditions.\
# If they are, we'll be replacing the values with a no-value flag. This is in preparation for clipping on \
# separations and velocity differences
MAC.fillna(-99, inplace=True)

MAC['z1'] = MAC['z1'].astype(float)
MAC['z2'] = MAC['z2'].astype(float)


#for i,j in MAC.iterrows():
#    if ('Double-Peak' in MAC.at[i, 'Selection Method']) and (MAC.at[i, 'z1']==MAC.at[i, 'z2']):
#        print('True')

for i, row in MAC.iterrows():
    # Check if z1 and z2 are not -99
    if row['z1'] != -99 and row['z2'] != -99:
        try:
            # Perform the calculation for the row
            MAC.at[i, 'dV'] = (2.99e+5) * ((1 + row['z1'])**2 - (1 + row['z2'])**2) / ((1 + row['z1'])**2 + (1 + row['z2'])**2)
        except TypeError as e:
            # If a TypeError occurs, print the row index and the error
            print(f"Error at row {i}: {e}")
            print(row)

            
for i, row in MAC.iterrows():
    # Check if z1 and z2 are not -99
    if (row['Sep'] != -99) and (row['Sep'] != -99.0) and (row['z1']>0) and (row['Sep']>0):
        try:
            # Perform the calculation for the row
            row['Sep(kpc)'] = row['Sep']*cosmo.kpc_proper_per_arcmin(row['z1'])*(u.arcmin/u.kpc)*(1/60)
        except TypeError as e:
            # If a TypeError occurs, print the row index and the error
            print(f"Error at row {i}: {e}")
            print(row)


In [ ]:
MAC_bad1 = MAC[MAC['Sep(kpc)']>100]


In [ ]:
for i, row in MAC.iterrows():
    # Check if z1 and z2 are not -99
    try:
        # Perform the calculation for the row
        MAC_bad1 = MAC[MAC['Sep(kpc)']>100.0]
    except TypeError as e:
        # If a TypeError occurs, print the row index and the error
        print(f"Error at row {i}: {e}")
        print(row)

In [ ]:
#import pandas as pd

# Load your dataframe
#df = pd.read_csv('your_file.csv')  # Replace with your file path

# Function to check if a value is a float
def is_float(value):
    try:
        float(value)
        return True
    except ValueError:
        return False

# Create a new dataframe for problem rows
problem_rows = pd.DataFrame()

# Iterate over the rows
for index, row in MAC.iterrows():
    value = row['Sep(kpc)']  # Replace 'your_column' with the name of your column
    if not is_float(value) or value == -99:
        problem_rows = problem_rows.append(row)

# Now, 'problem_rows' contains all the rows that you need to examine
#print(problem_rows)

# Optionally, save the problem rows to a new CSV
#problem_rows.to_csv('problem_rows.csv', index=False)


In [ ]:
problem_rows

In [ ]:
#import pandas as pd

# Load your dataframe
#df = pd.read_csv('your_file.csv')  # Replace with your file path

# Function to check if a value is a float
def is_float(value):
    try:
        float(value)
        return True
    except ValueError:
        return False

# Create a new dataframe for problem rows
good_rows = pd.DataFrame()

# Iterate over the rows
for index, row in MAC.iterrows():
    value = row['Sep(kpc)']  # Replace 'your_column' with the name of your column
    if is_float(value) or value != -99 or value!=-99.0:
        good_rows = good_rows.append(row)

# Now, 'problem_rows' contains all the rows that you need to examine
#print(good_rows)

# Optionally, save the problem rows to a new CSV
#problem_rows.to_csv('problem_rows.csv', index=False)



In [ ]:
MAC['Sep(kpc)'] = MAC['Sep(kpc)'].astype(float)


In [ ]:
np.max(MAC['Sep(kpc)'])
#MAC

In [ ]:
MAC_bad1 = MAC[MAC['Sep(kpc)']>100.0]




In [ ]:
MAC_bad1

In [ ]:
len(good_rows)

In [ ]:
MAC_bad1 = good_rows[good_rows['Sep(kpc)']>100.0]



In [ ]:
# Function to check if a value in a column is a string
def is_string(value):
    return isinstance(value, str)

# Create a new dataframe for rows where the specified column contains a string
rows_with_string_in_column = pd.DataFrame()

# Name of the column to check
column_name = 'Sep(kpc)'  # Replace 'your_column' with the name of your column

# Iterate over the rows
for index, row in MAC.iterrows():
    if is_string(row[column_name]):
        rows_with_string_in_column = rows_with_string_in_column.append(row)

# 'rows_with_string_in_column' contains all the rows where the specified column has a string
print(rows_with_string_in_column)

# Optionally, save these rows to a new CSV
#rows_with_string_in_column.to_csv('rows_with_string_in_column.csv', index=False)


In [ ]:
len(problem_rows)


In [ ]:
problem_rows

In [ ]:
for index, row in MAC.iterrows():
    print(row['z1'].dtype,row['z2'].dtype)
    

In [ ]:
MAC

In [ ]:
cosmo.kpc_proper_per_arcmin(3)*(u.arcmin/u.kpc)*(1/60)

In [ ]:
# And here we're going to introduce the subjective flag for system confidence

# literature and Name 1 == HVGC-1 is highly unlikely to be a recoil
# Lens Candidate,WISE 0326-3122 is a lens candidate also based on Schechter+2017
# Lens Candidate,WISE 1051-1142 is a lens candidate also based on Schechter+2017

# we flagged IRAS 16474+3430 as a dual agn candidate but it might be a real dual!

# (Unlikely),PKS 0537-441 listed oth a binary uqasar and as a smbh binary candidate but i consider it to be a very \
# weak binary candidate

# / Lens,Q1208+1011 could still be a lens based on literature. Need to double check

# cdouble check QJ0240-343AB

# double check Q0101.8-3012

# double check FBQ 1633+3134


# PG 1553+113 angular separation is an upper limit on the separation (<)

# for 4C+22.25 there was a binary separation (kpc) limit range of lim0.04-0.08e-3

# for Mrk 231 there was an angular limit of lim1e-3

# Tsai+2013's target was listed as having a 1pc separation....

# the Zhou+2004 ; Jaiswal+2019 target evidently had a matxch with another catalog and I'd previously listed multiple\
# separations.



In [ ]:
# now we'll work to format the selection methodology cell

types = MAC['Selection Method'].dropna().str.split(' / ')

# Step 2 and 3: Remove duplicates and alphabetize for each cell
def process_cell(cell):
    # Remove duplicates using set and then convert back to list
    unique_labels = list(set(cell))
    # Alphabetize the contents
    unique_labels.sort()
    return unique_labels

processed_types = types.apply(process_cell)

# Step 4: Join the contents back into a single string
MAC['Processed Selection Method'] = processed_types.apply(' / '.join)

# Display the updated DataFrame
print(MAC[['Processed Selection Method']])

In [ ]:
methods = MAC['Selection Method'].dropna().str.split(' / ')

# Flatten the lists and find unique labels
unique_methods = set(method for sublist in methods for method in sublist)

print("Unique selection methods:", unique_methods)
print(len(unique_methods))


In [ ]:
from astropy.table import Table


MAC1 = MAC.drop(['Notes'], axis=1)
t = Table.from_pandas(MAC1)

t.write('MAC_DR0p5_beta_webtable_11Dec2023.html', format='jsviewer', overwrite=True)



In [ ]:
MAC1